In [19]:
import pandas as pd
import numpy as np

import geopandas as gpd
from shapely.geometry import Point
import rtree
import pickle

import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
import statsmodels.formula.api as sm

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

from run_model import *
import gmaps
gmaps.configure(api_key=secret_key.google_api_key)

In [46]:
bike_df = load_pickle('storage/bike_df.pckl')
mta_df = load_pickle('storage/mta_df.pckl')

In [48]:
bike_df = bike_df[bike_df.zone != False]

In [50]:
bike_df['Start Time'] = pd.to_datetime(bike_df['Start Time'])
bike_df['day_of_week'] = bike_df['Start Time'].dt.weekday
bike_df['day_of_month'] = bike_df['Start Time'].dt.day

In [51]:
bike_df.head()

Trip Duration          Start Time           Stop Time  Start Station ID  \
0            680 2017-01-01 00:00:21 2017-01-01 00:11:41              3226   
1           1282 2017-01-01 00:00:45 2017-01-01 00:22:08              3263   
6            559 2017-01-01 00:05:00 2017-01-01 00:14:20               499   
8            255 2017-01-01 00:05:47 2017-01-01 00:10:02               430   
9            634 2017-01-01 00:07:34 2017-01-01 00:18:08              3165   

            Start Station Name  Start Station Latitude  \
0  W 82 St & Central Park West               40.782750   
1       Cooper Square & E 7 St               40.729236   
6           Broadway & W 60 St               40.769155   
8             York St & Jay St               40.701485   
9  Central Park West & W 72 St               40.775794   

   Start Station Longitude  End Station ID             End Station Name  \
0               -73.971370            3165  Central Park West & W 72 St   
1               -73.990868             498           Broadway & W 32 St   
6               -73.981918             479              9 Ave & W 45 St   
8               -73.986569             242   Carlton Ave & Flushing Ave   
9               -73.976206            3164       Columbus Ave & W 72 St   

   End Station Latitude  End Station Longitude  Bike ID   User Type  \
0             40.775794             -73.976206    25542  Subscriber   
1             40.748549             -73.988084    21136  Subscriber   
6             40.760193             -73.991255    27294  Subscriber   
8             40.697787             -73.973736    25041  Subscriber   
9             40.777057             -73.978985    16311  Subscriber   

   Birth Year  Gender  month  year  day_of_week  time_of_day        DATE  \
0      1965.0       2      1  2017            6            3  2017-01-01   
1      1987.0       2      1  2017            6            3  2017-01-01   
6      1973.0       1      1  2017            6            3  2017-01-01   
8      1989.0       1      1  2017            6            3  2017-01-01   
9      1980.0       1      1  2017            6            3  2017-01-01   

                                       zone  day_of_month  
0  81 ST - MUSEUM OF NATURAL HISTORY BC IND             1  
1                               8 ST NR BMT             1  
6                           59 ST ABCD1 IND             1  
8                             YORK ST F IND             1  
9                              72 ST BC IND             1

In [ ]:
data = pd.merge(bike_df, mta_df, on=['zone', 'DATE', 'time_of_day'])

In [ ]:
data.head()

In [ ]:
data.shape

In [ ]:
data.isnull().sum()

In [ ]:
plt.hist(test, bins=20, range=(0, 2));

In [ ]:
def plot_google_maps(locations, weights):
    locations = output[['lat', 'long']]
    #Get the magnitude from the data
    weights = output['error']

    fig = gmaps.figure()
    fig.add_layer(gmaps.heatmap_layer(locations, weights=weights))
    fig

In [ ]:
mta_loc[mta_loc.Station_Name == '103 ST']

In [ ]:
output[output.STATION == '125 ST']

In [ ]:
mta_loc

## Station Locations

In [ ]:
get_mta_loc()

In [2]:
mta_loc = load_pickle('storage/mta_loc.pckl')

In [3]:
mta_loc.head()

Station_Name Linename Division  Station_Latitude  Station_Longitude  \
0         1 AV        L      BMT         40.730953         -73.981628   
1       103 ST        1      IRT         40.799446         -73.968379   
2       103 ST        6      IRT         40.790600         -73.947478   
3       103 ST        7      IRT         40.749865         -73.862700   
4       103 ST       BC      IND         40.796092         -73.961454   

            zone  
0     1 AV L BMT  
1   103 ST 1 IRT  
2   103 ST 6 IRT  
3   103 ST 7 IRT  
4  103 ST BC IND

In [ ]:
weights = pd.DataFrame(np.ones(464))

In [ ]:
plot_google_maps(mta_loc[['Station_Latitude', "Station_Longitude"]], weight)

In [ ]:
locations = mta_loc[['Station_Latitude', "Station_Longitude"]]
    #Get the magnitude from the data


fig = gmaps.figure()
fig.add_layer(gmaps.heatmap_layer(locations, weights=weights))
fig

## MTA_DF

In [ ]:
mta_df = pd.read_csv("data/mta_turnstile/turnstile_170107.txt")
mta_df = mta_df.append(pd.read_csv("data/mta_turnstile/turnstile_170114.txt"))
mta_df = mta_df.append(pd.read_csv("data/mta_turnstile/turnstile_170121.txt"))
mta_df = mta_df.append(pd.read_csv("data/mta_turnstile/turnstile_170128.txt"))


## Bike_DF

In [ ]:
mta_loc['bike_station'] = 0

In [ ]:
mta_loc.head()

In [ ]:
mta_loc['bike_station'][0] == 0

In [ ]:
bike_df = pd.read_csv("data/201701-citibike-tripdata.csv.zip")

In [ ]:
def biketomtazone(coor):
    lat = coor[0]
    long = coor[1]
    bike_id = coor[2]
    
    for index, location in mta_loc.iterrows():
        station_lat = location['Station_Latitude']
        station_long = location['Station_Longitude']
        if( ((station_lat + 0.002000) >= lat)  and ((station_lat - 0.002000) <= lat) ):
            if( ((station_long + 0.003000) >= long) and ((station_long - 0.003000) <= long) ):
                if(mta_loc['bike_station'][index] == 0):
                    mta_loc['bike_station'][index] = bike_id
                    return location['zone']
                elif(mta_loc['bike_station'][index] == bike_id):
                    return location['zone']
    return False

In [ ]:
#     #left-top-corner
#     print(lat + 0.002000, ",",long - 0.003000)
    
#     #right-top-corner
#     print(lat + 0.002000, ",",long + 0.003000)
    
#     #right-bottom-corner
#     print(lat - 0.002000,",", long + 0.003000)
    
#     #left-bottom-corner
#     print(lat - 0.002000, ",",long - 0.003000)
    
# biketomtazone(40.782750, -73.971370)
# biketomtazone(40.776829, -73.963888)

In [ ]:
mini_bike = bike_df.head(200)

In [ ]:
import time 
start = time.time()
mini_bike['zone'] = mini_bike[['Start Station Latitude', 'Start Station Longitude', 'Start Station ID']].apply(biketomtazone,  axis=1)
print(time.time() - start)

In [ ]:
mini_bike

In [ ]:
mini_bike.groupby('zone')['Bike ID'].count()

In [ ]:
mini_bike[mini_bike.zone =='14 ST-UNION SQUARE LNQR456 IRT']

In [ ]:
mta_loc[mta_loc.zone == '14 ST-UNION SQUARE LNQR456 IRT']

In [1]:
pd.plotting.scatter_matrix(bike_df)

NameError: name 'pd' is not defined

In [ ]:
bike_df.head()


In [24]:
df = feature_engineering()

In [8]:
col = [ 'time_of_day', 'DELTA', '1 AV L BMT',
       '103 ST 1 IRT', '103 ST 6 IRT', '14 ST 123FLM IRT',
       '14 ST-UNION SQ 456LNQRW IRT', '15 ST-PROSPECT FG IND', '2 AV F IND',
       '21 ST-QNSBRIDGE F IND', '23 ST 1 IRT', '23 ST 6 IRT', '23 ST CE IND',
       '23 ST NRW BMT', '28 ST 6 IRT', '3 AV L BMT', '33 ST 6 IRT',
       '34 ST-HERALD SQ BDFMNQRW BMT', '34 ST-HUDSON YD 7 IRT',
       '34 ST-PENN STA 123 IRT', '4 AV-9 ST DFGMNR IND',
       '42 ST-BRYANT PK BDFM7 IND', '47-50 STS ROCK BDFM IND',
       '49 ST NQRW BMT', '5 AV/53 ST EM IND', '5 AV/59 ST NQRW BMT',
       '5 AVE 7BDFM IRT', '50 ST 1 IRT', '50 ST CE IND', '51 ST 6 IRT',
       '57 ST-7 AV NQRW BMT', '59 ST COLUMBUS 1ABCD IRT', '6 AV FLM123 BMT',
       '7 AV FG IND', '72 ST 123 IRT', '77 ST 6 IRT', '8 AV ACEL BMT',
       '8 ST-NYU NRW BMT', '86 ST 1 IRT', '86 ST BC IND', '96 ST 123 IRT',
       '96 ST 6 IRT', '96 ST BC IND', '9TH STREET 1 PTH',
       'ATL AV-BARCLAY 2345BDNQR IRT', 'B\'WAY-LAFAYETTE BDFQ6 IND',
       'BEDFORD AV L BMT', 'BEDFORD-NOSTRAN G IND', 'BERGEN ST 23 IRT',
       'BLEECKER ST 6DF IRT', 'BOROUGH HALL 2345R IRT',
       'BOROUGH HALL R2345 BMT', 'BOWERY JZ BMT', 'BOWLING GREEN 45 IRT',
       'CANAL ST ACE IND', 'CARROLL ST FG IND', 'CATHEDRAL PKWY 1 IRT',
       'CHAMBERS ST 123 IRT', 'CHRISTOPHER ST 1 IRT', 'CHRISTOPHER ST 1 PTH',
       'CITY / BUS 1 PTH', 'CLARK ST 23 IRT', 'CLASSON AV G IND',
       'CLINTON-WASH AV C IND', 'CORTLANDT ST RNW BMT', 'COURT SQ 7 IRT',
       'DEKALB AV BDNQR BMT', 'EAST BROADWAY F IND', 'FLUSHING AV G IND',
       'FRANKLIN AV 2345S IRT', 'FRANKLIN ST 1 IRT', 'GRAHAM AV L BMT',
       'GRAND ARMY PLAZ 23 IRT', 'GRAND ST BD IND', 'GRAND ST L BMT',
       'GRD CNTRL-42 ST 4567S IRT', 'GREENPOINT AV G IND', 'HIGH ST AC IND',
       'HOYT-SCHER ACG IND', 'KINGSTON-THROOP C IND',
       'LEXINGTON AV/53 EM6 IND', 'LEXINGTON AV/63 F IND', 'MONTROSE AV L BMT',
       'MYRTLE AV JMZ BMT', 'MYRTLE-WILLOUGH G IND', 'NEVINS ST 2345 IRT',
       'PRESIDENT ST 25 IRT', 'PRINCE ST NRW BMT', 'QUEENSBORO PLZ 7NQW IRT',
       'SMITH-9 ST FG IND', 'SPRING ST 6 IRT', 'SPRING ST CE IND',
       'UNION ST R BMT', 'VERNON-JACKSON 7 IRT', 'WALL ST 23 IRT']



In [25]:
df = df.sort_values('DATE')


rows = df.shape[0]

train = df.head(int(rows*0.8))
test = df.tail(int(rows*0.2))

## OLS Model

In [33]:
lin_model = sm.OLS(train['Bike ID'], train[col] )
result = lin_model.fit()
print(result.summary())
y_test = test['Bike ID']
y_pred = result.predict(test[col])

percent_error = (abs(y_pred - y_test + 1))/abs(y_test + 1)
print(np.mean(percent_error))

avg_error = (abs(y_pred - y_test + 1))
print(np.mean(avg_error))
test['pred'] = y_pred
test

                            OLS Regression Results                            
Dep. Variable:                Bike ID   R-squared:                       0.471
Model:                            OLS   Adj. R-squared:                  0.464
Method:                 Least Squares   F-statistic:                     66.28
Date:                Thu, 09 Aug 2018   Prob (F-statistic):               0.00
Time:                        13:46:08   Log-Likelihood:                -28867.
No. Observations:                6704   AIC:                         5.791e+04
Df Residuals:                    6614   BIC:                         5.853e+04
Df Model:                          89                                         
Covariance Type:            nonrobust                                         
                                   coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------------------------
time_of_day     

/home/iniyavan/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if sys.path[0] == '':


zone        DATE  time_of_day  Bike ID    DELTA  \
4785          CHRISTOPHER ST 1 IRT  2017-01-22           15       67   1731.0   
4786          CHRISTOPHER ST 1 IRT  2017-01-22           19       46   1691.0   
3780           BLEECKER ST 6DF IRT  2017-01-22            7       10     95.0   
3781           BLEECKER ST 6DF IRT  2017-01-22           11       29    467.0   
3782           BLEECKER ST 6DF IRT  2017-01-22           15      101    924.0   
3783           BLEECKER ST 6DF IRT  2017-01-22           19       92    912.0   
3784           BLEECKER ST 6DF IRT  2017-01-22           23       51    318.0   
4787          CHRISTOPHER ST 1 IRT  2017-01-22           23       27    888.0   
474                     2 AV F IND  2017-01-22            7        8    267.0   
7054         LEXINGTON AV/63 F IND  2017-01-22            7        2    697.0   
7056         LEXINGTON AV/63 F IND  2017-01-22           15       31   3582.0   
4017        BOROUGH HALL R2345 BMT  2017-01-22           11        4    111.0   
799                  23 ST NRW BMT  2017-01-22           23       14    531.0   
3292  ATL AV-BARCLAY 2345BDNQR IRT  2017-01-22           23       12   1122.0   
7285            NEVINS ST 2345 IRT  2017-01-22           23        3    411.0   
7284            NEVINS ST 2345 IRT  2017-01-22           19        4    862.0   
7283            NEVINS ST 2345 IRT  2017-01-22           15       10   1030.0   
7386           PRESIDENT ST 25 IRT  2017-01-22           15       10    277.0   
7387           PRESIDENT ST 25 IRT  2017-01-22           19        7    480.0   
1804                49 ST NQRW BMT  2017-01-22            7        1    363.0   
1439          4 AV-9 ST DFGMNR IND  2017-01-22           23        2    396.0   
1438          4 AV-9 ST DFGMNR IND  2017-01-22           19        5    637.0   
1437          4 AV-9 ST DFGMNR IND  2017-01-22           15        9    516.0   
1436          4 AV-9 ST DFGMNR IND  2017-01-22           11        5    246.0   
1805                49 ST NQRW BMT  2017-01-22           11       10   2035.0   
4018        BOROUGH HALL R2345 BMT  2017-01-22           15       20    350.0   
7622       QUEENSBORO PLZ 7NQW IRT  2017-01-22           15        6    513.0   
7623       QUEENSBORO PLZ 7NQW IRT  2017-01-22           19        3    560.0   
1806                49 ST NQRW BMT  2017-01-22           15        7   3541.0   
8107                UNION ST R BMT  2017-01-22           15       11    868.0   
8108                UNION ST R BMT  2017-01-22           19        9    936.0   
8109                UNION ST R BMT  2017-01-22           23        7    457.0   
928                     3 AV L BMT  2017-01-22            7        2    116.0   
2319                   51 ST 6 IRT  2017-01-22           11        6   1425.0   
2712               6 AV FLM123 BMT  2017-01-22           23       15    171.0   
2318                   51 ST 6 IRT  2017-01-22            7        1    334.0   
7385           PRESIDENT ST 25 IRT  2017-01-22           11        5    237.0   
7621       QUEENSBORO PLZ 7NQW IRT  2017-01-22           11        4    331.0   
5137               CLARK ST 23 IRT  2017-01-22           15       30      0.0   
5138               CLARK ST 23 IRT  2017-01-22           19        8      2.0   
1807                49 ST NQRW BMT  2017-01-22           19       24   3736.0   
5139               CLARK ST 23 IRT  2017-01-22           23        6      0.0   
797                  23 ST NRW BMT  2017-01-22           15       53   2006.0   
798                  23 ST NRW BMT  2017-01-22           19       26   1715.0   
2322                   51 ST 6 IRT  2017-01-22           23       11    879.0   
932                     3 AV L BMT  2017-01-22           23       44    536.0   
931                     3 AV L BMT  2017-01-22           19       52   1152.0   
930                     3 AV L BMT  2017-01-22           15       77   1999.0   
929                     3 AV L BMT  2017-01-22           11  

1.1968615720936364
13.78369686216891


In [10]:
rfrmodel = RandomForestRegressor(n_estimators=20, n_jobs=-1)
reg = rfrmodel.fit(train[col], train['Bike ID'])

print(rfrmodel.feature_importances_)
training_accuracy = reg.score(train[col], train['Bike ID'])
test_accuracy = reg.score(test[col], test['Bike ID'])

log_error = mean_squared_log_error(test['Bike ID'], rfrmodel.predict(test[col]))

print("############# based on standard predict ################")
print("R^2 on training data: %0.4f" % (training_accuracy))
print("R^2 on test data:     %0.4f" % (test_accuracy))
print("log on test data:     %0.4f" % (log_error))

y_test = test['Bike ID']
y_pred = rfrmodel.predict(test[col])

percent_error = (abs(y_pred - y_test + 1))/abs(y_test + 1)
print(np.mean(percent_error))

avg_error = (abs(y_pred - y_test + 1))
print(np.mean(avg_error))

test['percent_error'] = percent_error
test['avg_error'] = avg_error


[7.12569497e-02 5.24562895e-01 2.82582036e-03 0.00000000e+00
 7.16716224e-08 1.06257580e-02 2.48135281e-06 5.00388090e-05
 2.11725608e-02 1.36029414e-04 0.00000000e+00 1.96635482e-05
 1.00457752e-02 6.57887022e-03 0.00000000e+00 1.35194774e-02
 2.52015620e-04 2.84925945e-02 3.05868131e-04 2.61952776e-02
 9.90518010e-05 5.73019928e-03 2.22619300e-03 1.08761834e-03
 1.88478934e-07 2.87048914e-05 1.79255787e-02 9.14817725e-04
 9.87460652e-03 3.51789674e-03 1.37069581e-02 3.02614844e-03
 6.03837172e-03 0.00000000e+00 5.90625553e-07 4.82621819e-07
 0.00000000e+00 5.48069674e-02 1.93925202e-05 2.10543894e-04
 3.81676546e-07 4.26211714e-07 1.23470616e-03 8.36625988e-03
 6.27524179e-03 1.50389998e-07 3.49784638e-03 4.59932924e-05
 1.16909689e-03 3.92494295e-02 2.05302644e-03 5.46592113e-04
 2.18623246e-02 3.23192768e-03 4.74814255e-03 3.79943648e-04
 1.30913082e-07 1.01794889e-02 4.68823164e-03 1.41947676e-02
 6.26454812e-03 1.24664416e-03 6.47596538e-05 1.07184455e-03
 1.09617431e-07 7.081965

/home/iniyavan/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/home/iniyavan/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [14]:
test

zone        DATE  time_of_day  Bike ID    DELTA  \
4785          CHRISTOPHER ST 1 IRT  2017-01-22           15       67   1731.0   
4786          CHRISTOPHER ST 1 IRT  2017-01-22           19       46   1691.0   
3780           BLEECKER ST 6DF IRT  2017-01-22            7       10     95.0   
3781           BLEECKER ST 6DF IRT  2017-01-22           11       29    467.0   
3782           BLEECKER ST 6DF IRT  2017-01-22           15      101    924.0   
3783           BLEECKER ST 6DF IRT  2017-01-22           19       92    912.0   
3784           BLEECKER ST 6DF IRT  2017-01-22           23       51    318.0   
4787          CHRISTOPHER ST 1 IRT  2017-01-22           23       27    888.0   
474                     2 AV F IND  2017-01-22            7        8    267.0   
7054         LEXINGTON AV/63 F IND  2017-01-22            7        2    697.0   
7056         LEXINGTON AV/63 F IND  2017-01-22           15       31   3582.0   
4017        BOROUGH HALL R2345 BMT  2017-01-22           11        4    111.0   
799                  23 ST NRW BMT  2017-01-22           23       14    531.0   
3292  ATL AV-BARCLAY 2345BDNQR IRT  2017-01-22           23       12   1122.0   
7285            NEVINS ST 2345 IRT  2017-01-22           23        3    411.0   
7284            NEVINS ST 2345 IRT  2017-01-22           19        4    862.0   
7283            NEVINS ST 2345 IRT  2017-01-22           15       10   1030.0   
7386           PRESIDENT ST 25 IRT  2017-01-22           15       10    277.0   
7387           PRESIDENT ST 25 IRT  2017-01-22           19        7    480.0   
1804                49 ST NQRW BMT  2017-01-22            7        1    363.0   
1439          4 AV-9 ST DFGMNR IND  2017-01-22           23        2    396.0   
1438          4 AV-9 ST DFGMNR IND  2017-01-22           19        5    637.0   
1437          4 AV-9 ST DFGMNR IND  2017-01-22           15        9    516.0   
1436          4 AV-9 ST DFGMNR IND  2017-01-22           11        5    246.0   
1805                49 ST NQRW BMT  2017-01-22           11       10   2035.0   
4018        BOROUGH HALL R2345 BMT  2017-01-22           15       20    350.0   
7622       QUEENSBORO PLZ 7NQW IRT  2017-01-22           15        6    513.0   
7623       QUEENSBORO PLZ 7NQW IRT  2017-01-22           19        3    560.0   
1806                49 ST NQRW BMT  2017-01-22           15        7   3541.0   
8107                UNION ST R BMT  2017-01-22           15       11    868.0   
8108                UNION ST R BMT  2017-01-22           19        9    936.0   
8109                UNION ST R BMT  2017-01-22           23        7    457.0   
928                     3 AV L BMT  2017-01-22            7        2    116.0   
2319                   51 ST 6 IRT  2017-01-22           11        6   1425.0   
2712               6 AV FLM123 BMT  2017-01-22           23       15    171.0   
2318                   51 ST 6 IRT  2017-01-22            7        1    334.0   
7385           PRESIDENT ST 25 IRT  2017-01-22           11        5    237.0   
7621       QUEENSBORO PLZ 7NQW IRT  2017-01-22           11        4    331.0   
5137               CLARK ST 23 IRT  2017-01-22           15       30      0.0   
5138               CLARK ST 23 IRT  2017-01-22           19        8      2.0   
1807                49 ST NQRW BMT  2017-01-22           19       24   3736.0   
5139               CLARK ST 23 IRT  2017-01-22           23        6      0.0   
797                  23 ST NRW BMT  2017-01-22           15       53   2006.0   
798                  23 ST NRW BMT  2017-01-22           19       26   1715.0   
2322                   51 ST 6 IRT  2017-01-22           23       11    879.0   
932                     3 AV L BMT  2017-01-22           23       44    536.0   
931                     3 AV L BMT  2017-01-22           19       52   1152.0   
930                     3 AV L BMT  2017-01-22           15       77   1999.0   
929                     3 AV L BMT  2017-01-22           11  

In [5]:
percent_error = result[0]
avg_error = result[1]
df = result[2]

In [26]:
df = pd.merge(test, mta_loc, on='zone')

In [45]:
test = df.groupby(['Station_Latitude', 'Station_Longitude'])['avg_error'].mean().reset_index()

In [ ]:
plt.hist(avg_error);

In [46]:
locations = test[['Station_Latitude', 'Station_Longitude']]
#Get the magnitude from the data
weights = test['avg_error']

fig = gmaps.figure()
fig.add_layer(gmaps.heatmap_layer(locations, weights=weights))
fig

Figure(layout=FigureLayout(height='420px'))